<a href="https://colab.research.google.com/github/CodeGod420/Minecraft_agent/blob/main/Treechop_agent_CNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Tarea 3 SEM II
## Daniel Tapia 201704176-5


Esta es la versión desarrollada a base del template dispuesto por mineRL para generar un agente, en donde se instalan las bibliotecas necesarias, se decarga el dataset para el objetivo y se ejecutan en 2 secciones, una para el entrenamiento y otra para obtener acciones a base de un estado corriendo.



# Setup

In [ ]:
%%capture
# ^ hides output
!sudo add-apt-repository -y ppa:openjdk-r/ppa
!sudo apt-get purge openjdk-*
!sudo apt-get install openjdk-8-jdk
!sudo apt-get install xvfb xserver-xephyr vnc4server python-opengl ffmpeg
!pip3 install minerl==0.4.4
!pip3 install pyvirtualdisplay torch numpy
!pip3 install imageio==2.4.1
!pip3 install -U colabgymrender

# Launch virtual display, which is needed for MineRL
from pyvirtualdisplay import Display
display = Display(visible=0, size=(400, 300))
display.start();

In [ ]:
# Begin by downloading the dataset.
import minerl.data.download
minerl.data.download(directory='data', environment="MineRLTreechop-v0");

/usr/local/lib/python3.8/dist-packages/gym/logger.py:34: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize("%s: %s" % ("WARN", msg % args), "yellow"))
Download: https://minerl.s3.amazonaws.com/v4/MineRLTreechop-v0.tar: 100%|█████████▉| 1510.0/1510.73792 [02:15<00:00, 13.13MB/s]/usr/local/lib/python3.8/dist-packages/tqdm/std.py:533: TqdmWarning: clamping frac to range [0, 1]
  full_bar = Bar(frac,
Download: https://minerl.s3.amazonaws.com/v4/MineRLTreechop-v0.tar: 100%|██████████| 1511.0/1510.73792 [02:15<00:00, 11.15MB/s]


## Entrenamiento del modelo

En esta sección se detalla el codigo correspondiente a la implementación de behavioural cloning usando redes neuronales convolucionales.

In [ ]:
from tqdm import tqdm
import numpy as np
import torch as th
from torch import nn
import gym
import minerl
import cv2
from colabgymrender.recorder import Recorder
import logging
logging.disable(logging.ERROR)




class ConvNet(nn.Module):
    """
    :param input_shape: A three-item tuple telling image dimensions in (C, H, W)
    :param output_dim: Dimensionality of the output vector
    """

    def __init__(self, input_shape, output_dim):
        super().__init__()
        n_input_channels = input_shape[0]
        self.cnn = nn.Sequential(
            nn.Conv2d(n_input_channels, 32, kernel_size=8, stride=4, padding=0), #ver con stride si mejora la performance
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=4, stride=2, padding=0),
            nn.ReLU(),
            nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=0),
            nn.ReLU(),
            nn.Flatten(),
        )

        # Compute shape by doing one forward pass
        # ANSWER you can use this trick to get CNN output shape dynamically
        with th.no_grad():
            n_flatten = self.cnn(th.zeros(1, *input_shape)).shape[1]

        self.linear = nn.Sequential(
            nn.Linear(n_flatten, 512), #cambiar esto para ir probando el parametro n_flatten
            nn.ReLU(),
            nn.Linear(512, output_dim)
        )

    def forward(self, observations: th.Tensor) -> th.Tensor:
        # TODO with the layers you created in __init__, transform the `observations` (a tensor of shape (B, C, H, W)) to
        #      a tensor of shape (B, D), where D is the `output_dim`
        # ANSWER good olde' forward pass
        return self.linear(self.cnn(observations))


def environment_action_batch_to_agent_actions(dataset_actions):
    """
    Turn a batch of actions from environment (from BufferedBatchIterator) to a numpy
    array of agent actions.
    Agent actions _have to_ start from 0 and go up from there!
    For MineRLTreechop, you want to have actions for the following at the very least:
    - Forward movement
    - Jumping
    - Turning camera left, right, up and down
    - Attack
    For example, you could have seven agent actions that mean following:
    0 = forward
    1 = jump + forward
    2 = turn camera left
    3 = turn camera right
    4 = turn camera up
    5 = turn camera down
    6 = attack
    This should match `agent_action_to_environment`, by converting dictionary
    actions into individual integeres.
    If dataset action (dict) does not have a mapping to agent action (int),
    then set it "-1"
    """
    # There are dummy dimensions of shape one
    batch_size = len(dataset_actions["camera"])
    actions = np.zeros((batch_size,), dtype=np.int)

    for i in range(batch_size):
        # ANSWER map each action dict to actions described above,

        # ANSWER first check camera movement with a small margin
        # (Make camera movement be most important)
        if dataset_actions["camera"][i][0] < -5:
            actions[i] = 2
        elif dataset_actions["camera"][i][0] > 5:
            actions[i] = 3
        elif dataset_actions["camera"][i][1] > 5:
            actions[i] = 4
        elif dataset_actions["camera"][i][1] < -5:
            actions[i] = 5
        # ANSWER two different actions: "forward" and "forward-jump"
        elif dataset_actions["forward"][i] == 1:
            if dataset_actions["jump"][i] == 1:
                actions[i] = 1
            else:
                actions[i] = 0
        # ANSWER attack action
        elif dataset_actions["attack"][i] == 1:
            actions[i] = 6
        else:
            # No reasonable mapping (would be no-op)
            actions[i] = -1
    return actions


def train():
    # Path to where MineRL dataset resides (should contain "MineRLTreechop-v0" directory)
    DATA_DIR = "."
    # How many times we train over dataset and how large batches we use.
    # Larger batch size takes more memory but generally provides stabler learning.
    EPOCHS = 1
    BATCH_SIZE = 32

    # TODO create data iterators for going over MineRL Treechop-v0 data using BufferedBatchIterator
    #      https://minerl.readthedocs.io/en/latest/tutorials/data_sampling.html#sampling-the-dataset-with-buffered-batch-iter
    # ANSWER see below. Minimal dataset is downloaded automatically
    data = minerl.data.make("MineRLTreechop-v0", data_dir="data")
    iterator = minerl.data.BufferedBatchIter(data, buffer_target_size=10000)

    number_of_actions = 7
    # TODO we need to tell the network how many possible actions there are,
    #      so assign the value in above variable
    # ANSWER the number is defined by the action-mapping function above
    # (number of possible integers)

    network = ConvNet((3, 64, 64), number_of_actions).cuda()
    # TODO create optimizer and loss functions for training
    #      see examples here https://pytorch.org/tutorials/beginner/basics/optimization_tutorial.html
    # ANSWER below.
    optimizer = th.optim.Adam(network.parameters())
    loss_function = nn.CrossEntropyLoss()

    iter_count = 0
    losses = []
    for dataset_obs, dataset_actions, _, _, _ in tqdm(iterator.buffered_batch_iter(num_epochs=EPOCHS, batch_size=BATCH_SIZE)):
        # We only use camera observations here
        obs = dataset_obs["pov"].astype(np.float32)
        # Transpose observations to be channel-first (BCHW instead of BHWC)
        obs = obs.transpose(0, 3, 1, 2)
        # Normalize observations, otherwise the neural network will get spooked
        obs /= 255.0

        # Turn dataset actions into agent actions
        actions = environment_action_batch_to_agent_actions(dataset_actions)
        assert actions.shape == (obs.shape[0],), "Array from environment_action_batch_to_agent_actions should be of shape {}".format((obs.shape[0],))

        # Remove samples that had no corresponding action
        mask = actions != -1
        obs = obs[mask]
        actions = actions[mask]

        # TODO perform optimization step:
        # - Predict actions using the neural network (input is `obs`)
        # - Compute loss with the predictions and true actions. Store loss into variable `loss`
        # - Use optimizer to do a single update step
        # See https://pytorch.org/tutorials/beginner/basics/optimization_tutorial.html
        # for a tutorial
        # NOTE: Variables `obs` and `actions` are numpy arrays. You need to convert them into torch tensors.
        # ANSWER, below
        # Obtain logits of each action
        logits = network(th.from_numpy(obs).float().cuda())

        # Minimize cross-entropy with target labels.
        # We could also compute the probability of demonstration actions and
        # maximize them.
        loss = loss_function(logits, th.from_numpy(actions).long().cuda())

        # Standard PyTorch update
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # Keep track of how training is going by printing out the loss
        iter_count += 1
        losses.append(loss.item())
        if (iter_count % 1000) == 0:
            mean_loss = sum(losses) / len(losses)
            tqdm.write("Iteration {}. Loss {:<10.3f}".format(iter_count, mean_loss))
            losses.clear()

    # Store the network
    th.save(network, "behavioural_cloning.pth")

train()

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)3751936/45929032 bytes (8.2%)8093696/45929032 bytes (17.6%)12337152/45929032 bytes (26.9%)16605184/45929032 bytes (36.2%)20389888/45929032 bytes (44.4%)24666112/45929032 bytes (53.7%)28565504/45929032 bytes (62.2%)32956416/45929032 bytes (71.8%)35340288/45929032 bytes (76.9%)39075840/45929032 bytes (85.1%)42713088/45929032 bytes (93.0%)45929032/45929032 bytes (100.0%)
  Done
File saved as /root

0it [00:00, ?it/s]
100%|██████████| 1674/1674 [00:00<00:00, 98556.52it/s]

100%|██████████| 1635/1635 [00:00<00:00, 82209.71it/s]

100%|██████████| 1867/1867 [00:00<00:00, 98190.19it/s]

100%|██████████| 2215/2215 [00:00<00:00, 104196.67it/s]

100%|██████████| 2582/2582 [00:00<00:00, 90094.28it/s]
54it [00:12,  9.20it/s]
100%|██████████| 1494/1494 [00:00<00:00, 78422.73it/s]
91it [00:13, 18.64it/s]
100%|██████████| 2122/2122 [00:00<00:00, 14705.48it/s]
163it [00:14, 46.30it/s]
100%|██████████| 2230/2230 [00:00<00:00, 87353.59it/s]
234it [00:15, 68.50it/s]
100%|██████████| 1615/1615 [00:00<00:00, 84893.23it/s]
287it [00:16, 71.12it/s]
100%|██████████| 1950/1950 [00:00<00:00, 80119.24it/s]
338it [00:17, 63.63it/s]
100%|██████████| 2632/2632 [00:00<00:00, 82925.75it/s]
426it [00:19, 85.77it/s]
100%|██████████| 1863/1863 [00:00<00:00, 87276.90it/s]
496it [00:20, 85.36it/s]
100%|██████████| 2776/2776 [00:00<00:00, 87819.61it/s]
585it [00:22, 93.05it/s]
100%|██████████| 1680/1680 [00:00<00:0

Iteration 1000. Loss 0.976     



100%|██████████| 2194/2194 [00:00<00:00, 81088.99it/s]
1079it [00:31, 79.61it/s]
100%|██████████| 2729/2729 [00:00<00:00, 74602.95it/s]
1151it [00:33, 74.63it/s]
100%|██████████| 1384/1384 [00:00<00:00, 71282.82it/s]
1200it [00:33, 71.18it/s]
100%|██████████| 1655/1655 [00:00<00:00, 71680.85it/s]
1252it [00:34, 69.41it/s]
100%|██████████| 2255/2255 [00:00<00:00, 80449.75it/s]
1322it [00:36, 76.50it/s]
100%|██████████| 1669/1669 [00:00<00:00, 73266.21it/s]
1374it [00:37, 71.32it/s]
100%|██████████| 2038/2038 [00:00<00:00, 95466.69it/s]
1445it [00:38, 81.84it/s]
100%|██████████| 1830/1830 [00:00<00:00, 73275.89it/s]
1497it [00:39, 70.77it/s]
100%|██████████| 2523/2523 [00:00<00:00, 80383.37it/s]
1581it [00:41, 86.82it/s]
100%|██████████| 2413/2413 [00:00<00:00, 75969.85it/s]
1652it [00:42, 79.82it/s]
100%|██████████| 2441/2441 [00:00<00:00, 18522.84it/s]
1722it [00:43, 73.29it/s]
100%|██████████| 1570/1570 [00:00<00:00, 52507.81it/s]
1775it [00:44, 71.10it/s]
100%|██████████| 2460/2460 

Iteration 2000. Loss 0.832     


...

12035it [03:54, 77.22it/s]
100%|██████████| 1606/1606 [00:00<00:00, 65249.06it/s]
12085it [03:55, 70.98it/s]
100%|██████████| 1717/1717 [00:00<00:00, 11965.51it/s]
12152it [03:56, 79.72it/s]
100%|██████████| 3531/3531 [00:00<00:00, 83723.90it/s]
12257it [03:58, 94.83it/s]
100%|██████████| 1574/1574 [00:00<00:00, 74053.11it/s]
12311it [03:59, 79.48it/s]
100%|██████████| 3615/3615 [00:00<00:00, 83825.79it/s]
12414it [04:01, 104.64it/s]
100%|██████████| 1739/1739 [00:00<00:00, 69793.36it/s]
12467it [04:02, 74.38it/s]
100%|██████████| 2853/2853 [00:00<00:00, 86108.05it/s]
12554it [04:03, 87.35it/s]
100%|██████████| 1520/1520 [00:00<00:00, 59014.01it/s]
12605it [04:04, 74.69it/s]
100%|██████████| 3017/3017 [00:00<00:00, 85355.54it/s]
12708it [04:06, 107.07it/s]
100%|██████████| 2115/2115 [00:00<00:00, 79237.48it/s]
12760it [04:07, 69.90it/s]
100%|██████████| 2001/2001 [00:00<00:00, 83362.82it/s]
12831it [04:08, 82.06it/s]
100%|██████████| 1985/1985 [00:00<00:00, 15481.19it/s]
12900it [04:10

Iteration 13000. Loss 0.799     


13036it [04:12, 79.42it/s]
100%|██████████| 1790/1790 [00:00<00:00, 74118.21it/s]
13086it [04:13, 71.06it/s]
100%|██████████| 1417/1417 [00:00<00:00, 68522.05it/s]
13135it [04:14, 74.90it/s]
100%|██████████| 1766/1766 [00:00<00:00, 89018.51it/s]
13182it [04:15, 66.82it/s]
100%|██████████| 2144/2144 [00:00<00:00, 75006.36it/s]
13250it [04:16, 74.36it/s]
100%|██████████| 1573/1573 [00:00<00:00, 76066.64it/s]
13301it [04:17, 73.16it/s]
100%|██████████| 1703/1703 [00:00<00:00, 67361.06it/s]
13367it [04:18, 84.68it/s]
100%|██████████| 2159/2159 [00:00<00:00, 71179.30it/s]
13432it [04:19, 79.40it/s]
100%|██████████| 2014/2014 [00:00<00:00, 76524.67it/s]
13483it [04:21, 64.76it/s]
100%|██████████| 2556/2556 [00:00<00:00, 77301.54it/s]
13568it [04:22, 83.60it/s]
100%|██████████| 1718/1718 [00:00<00:00, 14431.31it/s]
13619it [04:23, 69.42it/s]
100%|██████████| 2457/2457 [00:00<00:00, 68170.52it/s]
13705it [04:24, 95.39it/s]
100%|██████████| 1630/1630 [00:00<00:00, 73889.67it/s]
13753it [04:25, 

Iteration 14000. Loss 0.730     


14053it [04:28, 52.39it/s] 


## Enjoy trained model

After training the model, fix the code below to load up the trained model and play games with it.


In [ ]:


def agent_action_to_environment(noop_action, agent_action):
    """
    Turn an agent action (an integer) into an environment action.
    This should match `environment_action_batch_to_agent_actions`,
    e.g. if attack=1 action was mapped to agent_action=0, then agent_action=0
    should be mapped back to attack=1.

    noop_action is a MineRL action that does nothing. You may want to
    use this as a template for the action you return.
    """
    # ANSWER this should be reverse of `environment_action_batch_to_agent_actions`
    action = noop_action
    if agent_action == 0:
        action["forward"] = 1
    elif agent_action == 1:
        action["forward"] = 1
        action["jump"] = 1
    elif agent_action == 2:
        action["camera"][0] = -5
    elif agent_action == 3:
        action["camera"][0] = 5
    elif agent_action == 4:
        action["camera"][1] = -5
    elif agent_action == 5:
        action["camera"][1] = 5
    elif agent_action == 6:
        action["attack"] = 1
    return action


# Load up the trained network
network = th.load("behavioural_cloning.pth").cuda()

env = gym.make('MineRLTreechop-v0')
env = Recorder(env, './video', fps=30)
# Play 3 games with the model
for game_i in range(3):
    obs = env.reset()
    done = False
    reward_sum = 0
    while not done:
        # TODO Process the observation:
        #   - Take only the camera observation
        #   - Add/remove batch dimensions
        #   - Transpose image (needs to be channels-last)
        #   - Normalize image
        #   - Store network output to `logits`
        # For hints, see what preprocessing was done during training
        # ANSWER see below
        # Transpose, add batch dim, normalize, turn into torch tensor
        obs = th.from_numpy(obs["pov"].transpose(2, 0, 1)[None].astype(np.float32) / 255.0).cuda()
        logits = network(obs)[0]
        # Turn logits into probabilities
        probabilities = th.softmax(logits, dim=0)
        # Into numpy
        probabilities = probabilities.detach().cpu().numpy()
        # TODO Pick an action based from the probabilities above.
        # The `probabilities` vector tells the probability of choosing one of the agent actions.
        # You have two options:
        # 1) Pick action with the highest probability
        # 2) Sample action based on probabilities
        # Option 2 works better emperically.
        # ANSWER pick action randomly below
        agent_action = np.random.choice(np.arange(probabilities.shape[0]), p=probabilities)

        noop_action = env.action_space.noop()
        environment_action = agent_action_to_environment(noop_action, agent_action)

        obs, reward, done, info = env.step(environment_action)
        reward_sum += reward
    print("Game {}, total reward {}".format(game_i, reward_sum))

env.release()
env.play()
env.close()

Game 0, total reward 1.0
Game 1, total reward 13.0
Game 2, total reward 14.0


# Cambiando la elección de la acción a la mas alta probabilidad

In [ ]:


def agent_action_to_environment(noop_action, agent_action):
    """
    Turn an agent action (an integer) into an environment action.
    This should match `environment_action_batch_to_agent_actions`,
    e.g. if attack=1 action was mapped to agent_action=0, then agent_action=0
    should be mapped back to attack=1.

    noop_action is a MineRL action that does nothing. You may want to
    use this as a template for the action you return.
    """
    # ANSWER this should be reverse of `environment_action_batch_to_agent_actions`
    action = noop_action
    if agent_action == 0:
        action["forward"] = 1
    elif agent_action == 1:
        action["forward"] = 1
        action["jump"] = 1
    elif agent_action == 2:
        action["camera"][0] = -5
    elif agent_action == 3:
        action["camera"][0] = 5
    elif agent_action == 4:
        action["camera"][1] = -5
    elif agent_action == 5:
        action["camera"][1] = 5
    elif agent_action == 6:
        action["attack"] = 1
    return action


# Load up the trained network
network = th.load("behavioural_cloning.pth").cuda()

env = gym.make('MineRLTreechop-v0')
env = Recorder(env, './video', fps=30)
# Play 3 games with the model
for game_i in range(3):
    obs = env.reset()
    done = False
    reward_sum = 0
    while not done:
        # TODO Process the observation:
        #   - Take only the camera observation
        #   - Add/remove batch dimensions
        #   - Transpose image (needs to be channels-last)
        #   - Normalize image
        #   - Store network output to `logits`
        # For hints, see what preprocessing was done during training
        # ANSWER see below
        # Transpose, add batch dim, normalize, turn into torch tensor
        obs = th.from_numpy(obs["pov"].transpose(2, 0, 1)[None].astype(np.float32) / 255.0).cuda()
        logits = network(obs)[0]
        # Turn logits into probabilities
        probabilities = th.softmax(logits, dim=0)
        # Into numpy
        probabilities = probabilities.detach().cpu().numpy()
        # TODO Pick an action based from the probabilities above.
        # The `probabilities` vector tells the probability of choosing one of the agent actions.
        # You have two options:
        # 1) Pick action with the highest probability
        # 2) Sample action based on probabilities
        # Option 2 works better emperically.
        # ANSWER pick action randomly below
        agent_action = np.amax(np.arange(probabilities.shape[0]))

        noop_action = env.action_space.noop()
        environment_action = agent_action_to_environment(noop_action, agent_action)

        obs, reward, done, info = env.step(environment_action)
        reward_sum += reward
    print("Game {}, total reward {}".format(game_i, reward_sum))

env.release()
env.play()
env.close()

# Variando parametro n_flatten


In [ ]:
from tqdm import tqdm
import numpy as np
import torch as th
from torch import nn
import gym
import minerl
import cv2
from colabgymrender.recorder import Recorder
import logging
logging.disable(logging.ERROR)




class ConvNet(nn.Module):
    """
    :param input_shape: A three-item tuple telling image dimensions in (C, H, W)
    :param output_dim: Dimensionality of the output vector
    """

    def __init__(self, input_shape, output_dim):
        super().__init__()
        n_input_channels = input_shape[0]
        self.cnn = nn.Sequential(
            nn.Conv2d(n_input_channels, 32, kernel_size=8, stride=2, padding=0), #ver con stride si mejora la performance
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=4, stride=2, padding=0),
            nn.ReLU(),
            nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=0),
            nn.ReLU(),
            nn.Flatten(),
        )

        # Compute shape by doing one forward pass
        # ANSWER you can use this trick to get CNN output shape dynamically
        with th.no_grad():
            n_flatten = self.cnn(th.zeros(1, *input_shape)).shape[1]

        self.linear = nn.Sequential(
            nn.Linear(n_flatten, 200), #cambiar esto para ir probando el parametro n_flatten
            nn.ReLU(),
            nn.Linear(200, output_dim)
        )

    def forward(self, observations: th.Tensor) -> th.Tensor:
        # TODO with the layers you created in __init__, transform the `observations` (a tensor of shape (B, C, H, W)) to
        #      a tensor of shape (B, D), where D is the `output_dim`
        # ANSWER good olde' forward pass
        return self.linear(self.cnn(observations))


def environment_action_batch_to_agent_actions(dataset_actions):
    """
    Turn a batch of actions from environment (from BufferedBatchIterator) to a numpy
    array of agent actions.
    Agent actions _have to_ start from 0 and go up from there!
    For MineRLTreechop, you want to have actions for the following at the very least:
    - Forward movement
    - Jumping
    - Turning camera left, right, up and down
    - Attack
    For example, you could have seven agent actions that mean following:
    0 = forward
    1 = jump + forward
    2 = turn camera left
    3 = turn camera right
    4 = turn camera up
    5 = turn camera down
    6 = attack
    This should match `agent_action_to_environment`, by converting dictionary
    actions into individual integeres.
    If dataset action (dict) does not have a mapping to agent action (int),
    then set it "-1"
    """
    # There are dummy dimensions of shape one
    batch_size = len(dataset_actions["camera"])
    actions = np.zeros((batch_size,), dtype=np.int)

    for i in range(batch_size):
        # ANSWER map each action dict to actions described above,

        # ANSWER first check camera movement with a small margin
        # (Make camera movement be most important)
        if dataset_actions["camera"][i][0] < -5:
            actions[i] = 2
        elif dataset_actions["camera"][i][0] > 5:
            actions[i] = 3
        elif dataset_actions["camera"][i][1] > 5:
            actions[i] = 4
        elif dataset_actions["camera"][i][1] < -5:
            actions[i] = 5
        # ANSWER two different actions: "forward" and "forward-jump"
        elif dataset_actions["forward"][i] == 1:
            if dataset_actions["jump"][i] == 1:
                actions[i] = 1
            else:
                actions[i] = 0
        # ANSWER attack action
        elif dataset_actions["attack"][i] == 1:
            actions[i] = 6
        else:
            # No reasonable mapping (would be no-op)
            actions[i] = -1
    return actions


def train():
    # Path to where MineRL dataset resides (should contain "MineRLTreechop-v0" directory)
    DATA_DIR = "."
    # How many times we train over dataset and how large batches we use.
    # Larger batch size takes more memory but generally provides stabler learning.
    EPOCHS = 1
    BATCH_SIZE = 32

    # TODO create data iterators for going over MineRL Treechop-v0 data using BufferedBatchIterator
    #      https://minerl.readthedocs.io/en/latest/tutorials/data_sampling.html#sampling-the-dataset-with-buffered-batch-iter
    # ANSWER see below. Minimal dataset is downloaded automatically
    data = minerl.data.make("MineRLTreechop-v0", data_dir="data")
    iterator = minerl.data.BufferedBatchIter(data, buffer_target_size=10000)

    number_of_actions = 7
    # TODO we need to tell the network how many possible actions there are,
    #      so assign the value in above variable
    # ANSWER the number is defined by the action-mapping function above
    # (number of possible integers)

    network = ConvNet((3, 64, 64), number_of_actions).cuda()
    # TODO create optimizer and loss functions for training
    #      see examples here https://pytorch.org/tutorials/beginner/basics/optimization_tutorial.html
    # ANSWER below.
    optimizer = th.optim.Adam(network.parameters())
    loss_function = nn.CrossEntropyLoss()

    iter_count = 0
    losses = []
    for dataset_obs, dataset_actions, _, _, _ in tqdm(iterator.buffered_batch_iter(num_epochs=EPOCHS, batch_size=BATCH_SIZE)):
        # We only use camera observations here
        obs = dataset_obs["pov"].astype(np.float32)
        # Transpose observations to be channel-first (BCHW instead of BHWC)
        obs = obs.transpose(0, 3, 1, 2)
        # Normalize observations, otherwise the neural network will get spooked
        obs /= 255.0

        # Turn dataset actions into agent actions
        actions = environment_action_batch_to_agent_actions(dataset_actions)
        assert actions.shape == (obs.shape[0],), "Array from environment_action_batch_to_agent_actions should be of shape {}".format((obs.shape[0],))

        # Remove samples that had no corresponding action
        mask = actions != -1
        obs = obs[mask]
        actions = actions[mask]

        # TODO perform optimization step:
        # - Predict actions using the neural network (input is `obs`)
        # - Compute loss with the predictions and true actions. Store loss into variable `loss`
        # - Use optimizer to do a single update step
        # See https://pytorch.org/tutorials/beginner/basics/optimization_tutorial.html
        # for a tutorial
        # NOTE: Variables `obs` and `actions` are numpy arrays. You need to convert them into torch tensors.
        # ANSWER, below
        # Obtain logits of each action
        logits = network(th.from_numpy(obs).float().cuda())

        # Minimize cross-entropy with target labels.
        # We could also compute the probability of demonstration actions and
        # maximize them.
        loss = loss_function(logits, th.from_numpy(actions).long().cuda())

        # Standard PyTorch update
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # Keep track of how training is going by printing out the loss
        iter_count += 1
        losses.append(loss.item())
        if (iter_count % 1000) == 0:
            mean_loss = sum(losses) / len(losses)
            tqdm.write("Iteration {}. Loss {:<10.3f}".format(iter_count, mean_loss))
            losses.clear()

    # Store the network
    th.save(network, "behavioural_cloning.pth")

train()

In [ ]:


def agent_action_to_environment(noop_action, agent_action):
    """
    Turn an agent action (an integer) into an environment action.
    This should match `environment_action_batch_to_agent_actions`,
    e.g. if attack=1 action was mapped to agent_action=0, then agent_action=0
    should be mapped back to attack=1.

    noop_action is a MineRL action that does nothing. You may want to
    use this as a template for the action you return.
    """
    # ANSWER this should be reverse of `environment_action_batch_to_agent_actions`
    action = noop_action
    if agent_action == 0:
        action["forward"] = 1
    elif agent_action == 1:
        action["forward"] = 1
        action["jump"] = 1
    elif agent_action == 2:
        action["camera"][0] = -5
    elif agent_action == 3:
        action["camera"][0] = 5
    elif agent_action == 4:
        action["camera"][1] = -5
    elif agent_action == 5:
        action["camera"][1] = 5
    elif agent_action == 6:
        action["attack"] = 1
    return action


# Load up the trained network
network = th.load("behavioural_cloning.pth").cuda()

env = gym.make('MineRLTreechop-v0')
env = Recorder(env, './video', fps=30)
# Play 3 games with the model
for game_i in range(3):
    obs = env.reset()
    done = False
    reward_sum = 0
    while not done:
        # TODO Process the observation:
        #   - Take only the camera observation
        #   - Add/remove batch dimensions
        #   - Transpose image (needs to be channels-last)
        #   - Normalize image
        #   - Store network output to `logits`
        # For hints, see what preprocessing was done during training
        # ANSWER see below
        # Transpose, add batch dim, normalize, turn into torch tensor
        obs = th.from_numpy(obs["pov"].transpose(2, 0, 1)[None].astype(np.float32) / 255.0).cuda()
        logits = network(obs)[0]
        # Turn logits into probabilities
        probabilities = th.softmax(logits, dim=0)
        # Into numpy
        probabilities = probabilities.detach().cpu().numpy()
        # TODO Pick an action based from the probabilities above.
        # The `probabilities` vector tells the probability of choosing one of the agent actions.
        # You have two options:
        # 1) Pick action with the highest probability
        # 2) Sample action based on probabilities
        # Option 2 works better emperically.
        # ANSWER pick action randomly below
        agent_action = np.random.choice(np.arange(probabilities.shape[0]), p=probabilities)

        noop_action = env.action_space.noop()
        environment_action = agent_action_to_environment(noop_action, agent_action)

        obs, reward, done, info = env.step(environment_action)
        reward_sum += reward
    print("Game {}, total reward {}".format(game_i, reward_sum))

env.release()
env.play()
env.close()

Game 0, total reward 2.0
Game 1, total reward 3.0
Game 2, total reward 10.0
